In [40]:
import pandas as pd
import json
import re

# Process ConvoKit (~15k)

In [41]:
with open('convokit/conversations.json') as fp:
    convos = json.load(fp)
print(f'There are {len(convos)} conversations')

# Get scores
scores = {}
with open('convokit/utterances.jsonl') as fp:
    for line in fp:
        info = json.loads(line)
        scores[info['id']] = info['meta']['score']

There are 15706 conversations


In [42]:
matcher = re.compile(r'\s*((?:\w|[^/])+)/+((?:\w|[^/])+)/+((?:\w|[^/])+)\s*\Z')
#matcher.match(all_posts[0]['title'])
match = matcher.match(' 2//3//4')
match.groups()

def clean_up(tokens):
    lines = [x.strip('\n\r\t ') for x in tokens]
    if all([l!= '' for l in lines]): 
        return lines
    else:
        return None

def process(text):
    text = text.strip('\n\r\t ')
    if '\n' in text:
        return None
    lines = None
    separators = ['//','/','\\','|',',']
    for sep in separators:
        split = text.split(sep)
        if len(split) == 3:
            return clean_up(split)
    return None
        
def process_and_join(text):
    processed = process(text)
    if processed is not None:
        return '/'.join(processed)
        

    

In [43]:
all_posts = []
skipped = 0
total = len(convos)
for i, (post_id, convo) in enumerate(convos.items()):
    if i % 100 == 0:
        print(f'Processing {i}/{len(convos)}')
    processed_title = process(convo['title'])
    if processed_title is None:
        skipped += 1
        print(f"Skipped: {convo['title']}")
        continue
    post_dict = {
        'id': post_id,
        #'title': convo['title'],
        'processed_title': '/'.join(processed_title),
        'score':scores[post_id],
        'created_utc': convo['timestamp']
    }
    # Filter and postprocess
    all_posts.append(post_dict)
    
print(f'Skipped {skipped}/{len(convos)}')
    
df = pd.DataFrame(all_posts, columns=['id', 'processed_title', 'score', 'created_utc'])
    #print(convo)

Processing 0/15706
Skipped: Writing haikus instead of studying for my two tests tomorrow. Sending them to friends who are probably fast asleep. Bastards.
Skipped: A poem for a planet: Send your haiku to Mars
Skipped: Meta Haiku
Skipped: No condoms? No problems.
Skipped: Muscles coil and spring. Feline hunter's instincts wake. Moth season is here.
Skipped: My Green Curry Haiku
Skipped: Jotted down 3 before bed
Skipped: Haiku request
Skipped: There is a fine line
Skipped: Let alone
Skipped: Lunch
Skipped: some hope
Skipped: a philosopher's haiku
Skipped: Penguin Haiku I-A Series I started recently &lt;(")
Skipped: Steel from my heart.
Skipped: Mosquito bites
Skipped: [Haiku] Running In White Neighborhood
Skipped: Political
Skipped: ghost
Skipped: Mystic battle
Skipped: Religious
Skipped: 3rd haiku I wrote in English class today
Skipped: The Weary Hermit
Skipped: /u/SubtlePineapple on catching things with your foot
Skipped: Meditating in the Grass
Skipped: I just pissed my pants. And thou

In [44]:
df = df.sort_values('score', ascending=False)
df.to_csv('convo.csv')

# Process My Reddit Dump (~5k)

In [45]:
import os
from glob import glob
df = {}
for file in glob('reddit-2022-10-20-dump/*.csv'):
    df[file] = pd.read_csv(file)
big_df = pd.concat(df.values())

In [46]:
print('Total', len(big_df), 'Unique', big_df.id.nunique())
big_df = big_df.groupby('id').first()

Total 3950 Unique 2376


In [47]:
# Clean up the data
big_df['processed_title'] = big_df['title'].apply(process_and_join)

In [48]:
big_df.iloc[20]

Unnamed: 0                                                       628
title              My sticky lover / Juices running down my chin ...
author_name                                        Matti_Matti_Matti
author_karma                                                  188262
ups                                                               31
downs                                                              0
upvote_ratio                                                    0.95
permalink          /r/haiku/comments/3s9bdd/my_sticky_lover_juice...
created_utc                                             1447151751.0
processed_title    My sticky lover/Juices running down my chin/Oh...
Name: 3s9bdd, dtype: object

In [49]:
big_df.sort_values(['ups','author_karma'],ascending=False)
big_df.to_csv('reddit-2022-10-20-dump.csv')

# Merge two datasets

In [50]:
mydump_df = pd.read_csv('reddit-2022-10-20-dump.csv')
convokit_df = pd.read_csv('convo.csv')
merged_df = pd.concat([mydump_df, convokit_df.rename(columns={'score':'ups'})])
print('No content?', merged_df.processed_title.isnull().sum())

No content? 63


In [51]:
# we assume convokit scores mean "ups"
merged_df = merged_df[['id', 'processed_title', 'ups']]
print(f'Total merged {len(merged_df)} unique ids {merged_df.id.nunique()}')
# Remove unique Ids
merged_df = merged_df.groupby('id').first()
merged_df = merged_df.dropna()
print(len(merged_df))
merged_df.to_csv('merged.csv')

Total merged 15449 unique ids 15344
15281


# Annotate with KeyBERT

In [72]:
from keybert import KeyBERT
from tqdm import tqdm
tqdm.pandas()

doc = """
         Supervised learning is the machine learning task of learning a function that
         maps an input to an output based on example input-output pairs. It infers a
         function from labeled training data consisting of a set of training examples.
         In supervised learning, each example is a pair consisting of an input object
         (typically a vector) and a desired output value (also called the supervisory signal).
         A supervised learning algorithm analyzes the training data and produces an inferred function,
         which can be used for mapping new examples. An optimal scenario will allow for the
         algorithm to correctly determine the class labels for unseen instances. This requires
         the learning algorithm to generalize from the training data to unseen situations in a
         'reasonable' way (see inductive bias).
      """
kw_model = KeyBERT()
keywords = kw_model.extract_keywords(doc)

def extract_keyword_from_haiku(processed_title):
    title = ', '.join(processed_title.split('/'))
    keywords = kw_model.extract_keywords(title)
    return keywords  # e.g. [('supervised', 0.6676),('labeled', 0.4896)]


In [73]:
df = pd.read_csv('merged.csv')
df['keywords'] = df.processed_title.progress_apply(extract_keyword_from_haiku)
df.to_csv('merged_with_keywords.csv')

100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 15281/15281 [10:43<00:00, 23.74it/s]


In [89]:
# Take top 5 keywords
keyword_based_json = {}
for row in tqdm(df.itertuples()):
    for i, (key,val) in enumerate(row.keywords):
        if i>=5:
            break
        keyword_based_json.setdefault(key, [])
        keyword_based_json[key].append(row.processed_title)
    #print(row)
final_json = {}
final_json['data'] = [{keyword:haikus} for keyword, haikus in keyword_based_json.items()]
with open('reddit_dataset.json', 'w') as fp:
    json.dump(final_json, fp, indent=4)

15281it [00:00, 261731.86it/s]


In [84]:
keyword_based_json

{'inside': list}